# Korpus einlesen: Wikipedia, Duck. AI, ipynb


gegeben:

* Ein Text, der mit Überschriften gegliedert ist: [](#wikipedia)
* mehrere Chats, wie sie von duck.ai exportiert werden: [](#duck-ai)
* Ein ipynb, das in Zellen gegliedert ist: [](#ipynb)

gesucht:
* eine Datenstruktur, die uns diese und ähnlich strukturierte Dateien für das weitere Textmining gut zugänglich bereitstellt.

Idee:
* Lege die eingelesenen Daten in einer Struktur `corpus_dict` ab, aus der von `pd.DataFrame.from_dict(corpus_dict, orient="index")` in ein Pandas Dataframe generiert werden kann, gvl. https://pandas.pydata.org/docs/reference/api/pandas.DataFrame.from_dict.html
* Lege den Index dabei gleich so an, dass ein Pandas Multi Index entsteht: https://pandas.pydata.org/docs/user_guide/advanced.html

Dieses Notebook: Exploration verschiedener und im Detail leicht unterschiedlicher(!) logischer Strukturierungen (aber alle in einem Pandas DataFrame abgelegt).

Zur Diskussion im *FWPF Text Mining*: Wo wollen wir hin, was benötigen wir?


In [1]:
import pathlib
import pandas as pd

import os
import glob
import json
import regex as re
from zipfile import ZipFile

In [24]:
global_verbose = 2   # 0: keine Info-Ausgabe; 1: minimale informative Info-Ausgabe; 2: ganz viel Debug-Ouptut
default_ngram = 3

(wikipedia)=
## Wikipedia

In [3]:
#https://pypi.org/project/Wikipedia-API/
import wikipediaapi

class Wikipedia_page():
    def __init__(self, page_title, *, verbose = global_verbose):

        self.count = 0

        # API-Client initialisieren, Sprache auf Deutsch setzen
        wiki_wiki = wikipediaapi.Wikipedia(
            user_agent='J.Busse, HAW Landshut, jbusse@jbusse.de', 
            language='de'
        )
    
        self.page = wiki_wiki.page(page_title)
    
        if not self.page.exists():
            print(f"Die Seite '{self.page_title}' wurde nicht gefunden.")
            return
    
        print(f"Seiten-Titel: {self.page.title}")
        print(f"URL: {self.page.fullurl}")
        print("-" * 30)
               
        # Der Einleitungstext vor der ersten Überschrift ist in page.summary oder page.text
        self.sections = {}
        self.sections[ (self.page.fullurl, "0") ] = { "prompt": "summary", "answer": self.page.summary }
        #self.sections[ (self.page.fullurl, f"{self.page.title}_1") ] = { "prompt": "text", "answer": self.page.text }
    
        # print("* Einleitung")
        # print(f"  Inhalt: {page.summary[:100]}...")
        # Alle Hauptsektionen abrufen und ausgeben

        self.count = 1
        self.collect_sections(self.page.sections)

        # our data structure is fine if the following statement gives a meaningful result
        self.df = pd.DataFrame.from_dict(self.sections, orient="index")


    def collect_sections(self, sections, level=0):
        for section in sections:
            sect_id = (self.page.fullurl, f"{self.count}") # {level}_
            self.sections[sect_id] = { "prompt": section.title, "answer": section.text }
            self.count += 1
            if section.sections:
                self.collect_sections(section.sections, level + 1)
    

In [4]:
exmplwikipage = Wikipedia_page("Bodensee")

Seiten-Titel: Bodensee
URL: https://de.wikipedia.org/wiki/Bodensee
------------------------------


In [5]:
exmplwikipage.df

prompt  \
https://de.wikipedia.org/wiki/Bodensee 0                                 summary   
                                       1                              Geschichte   
                                       2                        Namensgeschichte   
                                       3                 Eckdaten zur Geschichte   
                                       4    Bodensee auf historischen Landkarten   
...                                                                          ...   
                                       103                            Geschichte   
                                       104                           Reiseführer   
                                       105                      Natur und Umwelt   
                                       106                             Bildbände   
                                       107                              Weblinks   

                                                                                       answer  
https://de.wikipedia.org/wiki/Bodensee 0    Der Bodensee ist ein Binnengewässer im südwest...  
                                       1    Nach dem Ende der letzten Kaltzeit vor circa 1...  
                                       2    Der römische Geograph Pomponius Mela nennt um ...  
                                       3    Aus der Altsteinzeit sind keine Funde in unmit...  
                                       4    Die älteste Darstellung des Bodensees stammt a...  
...                                                                                       ...  
                                       103  Karl Heinz Burmeister: Bodensee. In: Historisc...  
                                       104  Andreas Balze, Gerhard Fischer: Bodensee (= Du...  
                                       105  Annette Bernauer, Harald Jacoby: Bodensee. Nat...  
                                       106  Franz X. Bogner: Der Bodensee aus der Luft. St...  
                                       107  \nLiteratur von und über Bodensee im Katalog d...  

[108 rows x 2 columns]

(duck-ai)=
## Duck .AI

In [6]:
class Chat():
    def __init__(self, path, *, verbose = global_verbose):
        self.path = pathlib.Path(path)

        usertag = [ 'Benutzereingabe', 'Підказка користувача' ]
        
        # alle Elemente aus usertag in eine regex umbauen: 
        # 'Benutzereingabe' ODER 'Підказка користувача' ODER ... 
        regex_usertag = '|'.join(fr'\s+{tag}\s+' for tag in usertag)
        # print(f"DEBUG {regex=}")

        models =  [ 'Claude Haiku 3.5', 'GPT-4o mini', 'GPT-5 mini', 
            'GPT-OSS 120B', 'Llama 4 Scout', 'Mistral Small 3' ]
        # aus der Liste der bekannten Modelle eine regex bauen:
        # Claude Haiku 3.5' ODER 'GPT-4o mini' ODER 'GPT-5 mini' ODER ...
        # (die verfügbaren Modelle müssen dazu bekannt sein)
        regex_models = '|'.join(fr'\s+{tag}:\n' for tag in models) 
        # print(f"DEBUG {regex2=}")
        

        if verbose >=2 : print(f"INFO 11: reading {str(self.path)}", end = "")
        with open(self.path, 
                  "r",  # default
                  encoding="utf-8-sig"  # remove Byte Order Mark (BOM) if necessary
                 ) as p:
            self.fulltext = p.read()
        if verbose >= 2: print(f"... got {len(self.fulltext)} bytes")

        # fulltext in einzelne Frage-Antwort-Interaktionen aufsplitten
        self.raw_sections = re.split(regex_usertag, self.fulltext)

        # duck.ai generiert einen (leidlich uninteressanten) Kopf, der mit "======" endet.
        self.head = self.raw_sections.pop(0)

        # body: Darstellung des Chats als Tabelle
        # Jede Interaktion ist eine Zeile in der Tabelle
        # Implementierung wie bei https://pandas.pydata.org/docs/reference/api/pandas.DataFrame.from_dict.html
        # * initial mit den Spalten prompt, answer
        # * leicht erweiterbar durch zusätzliche Spalten wie clean, n-grams etc.

        self.sections = {}

        # für jede Interaktion
        for i in self.raw_sections:
            timestamp, text = i.split(':\n', 1)  # erste Zeile ist timestamp
            
            sect_id = (path,timestamp)
            self.sections[ sect_id ] = {}
            
            # Aufsplitten in Promt, Answer
            splt = re.split(regex_models, text, maxsplit=1)

            self.sections[ sect_id ]["prompt"] = splt[0]
            self.sections[ sect_id ]["answer"] = splt[1]

        # our data structure is fine if the following statement gives a meaningful result
        # generate a local df in order to show the result of our analysis steps. 
        self.df = pd.DataFrame.from_dict(self.sections, orient="index")
        
    def __repr__(self):
        return f"{str(self.path)} ({len(self.sections)})"

Welche Dateien haben wir?

Begriffliche Grundlagen "Datei", "Pfad" etc.: <https://miguendes.me/python-pathlib#the-anatomy-of-a-pathlibpath>, gute Abbildung: <https://cdn.hashnode.com/res/hashnode/image/upload/v1635494392030/uomUWH2vC.png>

In [7]:
import glob
corpus_folder = "../korpus_2025-10-17/"
corpus_glob_pattern = corpus_folder + "**/*"
files_path = glob.glob( corpus_glob_pattern )
if global_verbose >= 1:
    print(f"INFO 19: {corpus_glob_pattern=} found {len(files_path)} files")
    len(files_path), files_path[0:3]

INFO 19: corpus_glob_pattern='../korpus_2025-10-17/**/*' found 33 files


Für jede Datei aus `files_path` eine Instanz der Klasse `Chats` anlegen, in der dann alle Infos zusammengefasst sind.

In [8]:
corpus_list = [ Chat(path, verbose=0) for path in files_path ]

In [9]:
corpus_dict = {}

for chat in corpus_list:
    for sect_id, content in chat.sections.items(): 
        corpus_dict[sect_id] = content

corpus_dict.keys()

dict_keys([('../korpus_2025-10-17/claude-haiku-3.5/duck.ai_2025-10-17_10-48-19-claude.txt', '1 von 2 - 17.10.2025, 10:47:25'), ('../korpus_2025-10-17/claude-haiku-3.5/duck.ai_2025-10-17_10-48-19-claude.txt', '2 von 2 - 17.10.2025, 10:47:41'), ('../korpus_2025-10-17/claude-haiku-3.5/duck.ai_2025-10-17_10-50-29_regex_Claude_Haiku_3_5.txt', '1 з 2 - 17.10.2025, 10:49:54'), ('../korpus_2025-10-17/claude-haiku-3.5/duck.ai_2025-10-17_10-50-29_regex_Claude_Haiku_3_5.txt', '2 з 2 - 17.10.2025, 10:50:08'), ('../korpus_2025-10-17/claude-haiku-3.5/duck.ai_2025-10-17_10-51-26_Haiku35.txt', '1 von 2 - 17.10.2025, 10:50:30'), ('../korpus_2025-10-17/claude-haiku-3.5/duck.ai_2025-10-17_10-51-26_Haiku35.txt', '2 von 2 - 17.10.2025, 10:50:58'), ('../korpus_2025-10-17/claude-haiku-3.5/duck.ai_2025-10-17_10-48-24_claude-haiku.txt', '1 von 2 - 17.10.2025, 10:47:34'), ('../korpus_2025-10-17/claude-haiku-3.5/duck.ai_2025-10-17_10-48-24_claude-haiku.txt', '2 von 2 - 17.10.2025, 10:47:56'), ('../korpus_2025-10

In [10]:
corpus_df = pd.DataFrame.from_dict(corpus_dict, orient="index")

In [11]:
corpus_df.head()

prompt  \
../korpus_2025-10-17/claude-haiku-3.5/duck.ai_2... 1 von 2 - 17.10.2025, 10:47:25  Erkläre einem Kind in der Grundschule reguläre...   
                                                   2 von 2 - 17.10.2025, 10:47:41     Erkläre auf Hochschulniveau reguläre Ausdrücke   
../korpus_2025-10-17/claude-haiku-3.5/duck.ai_2... 1 з 2 - 17.10.2025, 10:49:54    Erkläre einem Kind in der Grundschule reguläre...   
                                                   2 з 2 - 17.10.2025, 10:50:08       Erkläre auf Hochschulniveau reguläre Ausdrücke   
../korpus_2025-10-17/claude-haiku-3.5/duck.ai_2... 1 von 2 - 17.10.2025, 10:50:30  Erkläre einem Kind in der Grundschule reguläre...   

                                                                                                                              answer  
../korpus_2025-10-17/claude-haiku-3.5/duck.ai_2... 1 von 2 - 17.10.2025, 10:47:25  ## Reguläre Ausdrücke für Kinder: Eine spieler...  
                                                   2 von 2 - 17.10.2025, 10:47:41  ## Reguläre Ausdrücke: Eine Tiefenanalyse für ...  
../korpus_2025-10-17/claude-haiku-3.5/duck.ai_2... 1 з 2 - 17.10.2025, 10:49:54    ## Reguläre Ausdrücke für Kinder: Eine spieler...  
                                                   2 з 2 - 17.10.2025, 10:50:08    ## Reguläre Ausdrücke: Formale Theorie und Pra...  
../korpus_2025-10-17/claude-haiku-3.5/duck.ai_2... 1 von 2 - 17.10.2025, 10:50:30  ## Reguläre Ausdrücke für Kinder: Eine einfach...

In [12]:
corpus_df.index

MultiIndex([(                         '../korpus_2025-10-17/claude-haiku-3.5/duck.ai_2025-10-17_10-48-19-claude.txt', ...),
            (                         '../korpus_2025-10-17/claude-haiku-3.5/duck.ai_2025-10-17_10-48-19-claude.txt', ...),
            (         '../korpus_2025-10-17/claude-haiku-3.5/duck.ai_2025-10-17_10-50-29_regex_Claude_Haiku_3_5.txt', ...),
            (         '../korpus_2025-10-17/claude-haiku-3.5/duck.ai_2025-10-17_10-50-29_regex_Claude_Haiku_3_5.txt', ...),
            (                        '../korpus_2025-10-17/claude-haiku-3.5/duck.ai_2025-10-17_10-51-26_Haiku35.txt', ...),
            (                        '../korpus_2025-10-17/claude-haiku-3.5/duck.ai_2025-10-17_10-51-26_Haiku35.txt', ...),
            (                   '../korpus_2025-10-17/claude-haiku-3.5/duck.ai_2025-10-17_10-48-24_claude-haiku.txt', ...),
            (                   '../korpus_2025-10-17/claude-haiku-3.5/duck.ai_2025-10-17_10-48-24_claude-haiku.txt', ...),
        

Für Debug- und Demo-Zwecke wollen wir uns eine beliebige, aber feste Instanz herauspicken:

In [13]:
example_chat = corpus_list[0]
example_chat.sections

{('../korpus_2025-10-17/claude-haiku-3.5/duck.ai_2025-10-17_10-48-19-claude.txt',
  '1 von 2 - 17.10.2025, 10:47:25'): {'prompt': 'Erkläre einem Kind in der Grundschule reguläre Ausdrücke',
  'answer': '## Reguläre Ausdrücke für Kinder: Eine spielerische Erklärung\n\n### Was sind reguläre Ausdrücke?\n\nStell dir vor, reguläre Ausdrücke sind wie <b>magische Suchzauber für Buchstaben und Wörter</b>. Sie helfen uns, ganz genau zu suchen und zu finden, was wir möchten - fast wie ein Detektiv, der einen geheimen Code knackt!\n\n### Einfache Erklärung mit einem Beispiel\n\nLass uns das mit einem Spiel erklären:\n\n#### Der Buchstaben-Schatzsuche-Zauber\n\nAngenommen, du möchtest in deinen Lieblingsbüchern nach Wörtern suchen:\n\n- <b>*a*</b> findet alle Wörter mit dem Buchstaben "a"\n- <b>*haus*</b> findet Wörter wie "Haus", "Bauhaus", "Hausaufgabe"\n- <b>*tier*</b> findet "Tier", "Abenteuer", "Viereck"\n\n### Lustige Suchregeln\n\n1. Manche Zeichen sind wie Joker:\n   - <b>*</b> bedeutet: E

In [14]:
example_chat.df

prompt  \
../korpus_2025-10-17/claude-haiku-3.5/duck.ai_2... 1 von 2 - 17.10.2025, 10:47:25  Erkläre einem Kind in der Grundschule reguläre...   
                                                   2 von 2 - 17.10.2025, 10:47:41     Erkläre auf Hochschulniveau reguläre Ausdrücke   

                                                                                                                              answer  
../korpus_2025-10-17/claude-haiku-3.5/duck.ai_2... 1 von 2 - 17.10.2025, 10:47:25  ## Reguläre Ausdrücke für Kinder: Eine spieler...  
                                                   2 von 2 - 17.10.2025, 10:47:41  ## Reguläre Ausdrücke: Eine Tiefenanalyse für ...

### Weitere Spalten erzeugen

Typische Aufgabe: In einem (hier natürlichsprachlichen) Text sollen nur noch sinntragende alphanumerische Zeichen enthalten sein. Alle anderen Zeichen -- insbesondere Sonderzeichen, aber auch "seltsame" utf8-Zeichen etc. -- sollen duech Leerzeichen ersetzt werden.

In [15]:
def clean(text):
    """Remove chars that are not isalnum(); condense subsequent spaces."""
    def alnum(x): return x if x.isalnum() else " "
    cleaned = "".join( alnum(c) for c in text)
    return " ".join(  [ word for word in cleaned.split() if len(word) > 1 ] )

In [16]:
corpus_df['cleaned'] = corpus_df['answer'].apply(clean)

In [17]:
corpus_df

prompt  \
../korpus_2025-10-17/claude-haiku-3.5/duck.ai_2... 1 von 2 - 17.10.2025, 10:47:25  Erkläre einem Kind in der Grundschule reguläre...   
                                                   2 von 2 - 17.10.2025, 10:47:41     Erkläre auf Hochschulniveau reguläre Ausdrücke   
../korpus_2025-10-17/claude-haiku-3.5/duck.ai_2... 1 з 2 - 17.10.2025, 10:49:54    Erkläre einem Kind in der Grundschule reguläre...   
                                                   2 з 2 - 17.10.2025, 10:50:08       Erkläre auf Hochschulniveau reguläre Ausdrücke   
../korpus_2025-10-17/claude-haiku-3.5/duck.ai_2... 1 von 2 - 17.10.2025, 10:50:30  Erkläre einem Kind in der Grundschule reguläre...   
                                                   2 von 2 - 17.10.2025, 10:50:58     Erkläre auf Hochschulniveau reguläre Ausdrücke   
../korpus_2025-10-17/claude-haiku-3.5/duck.ai_2... 1 von 2 - 17.10.2025, 10:47:34  Erkläre einem Kind in der Grundschule reguläre...   
                                                   2 von 2 - 17.10.2025, 10:47:56     Erkläre auf Hochschulniveau reguläre Ausdrücke   
../korpus_2025-10-17/claude-haiku-3.5/duck.ai_2... 1 von 2 - 17.10.2025, 10:49:33  Erkläre einem Kind in der Grundschule reguläre...   
                                                   2 von 2 - 17.10.2025, 10:49:52    Erkläre auf Hochschulniveau reguläre Ausdrücke.   
../korpus_2025-10-17/llama-4-scout/duck.ai_2025... 1 von 2 - 17.10.2025, 10:45:19  Erkläre einem Kind in der Grundschule reguläre...   
                                                   2 von 2 - 17.10.2025, 10:45:44     Erkläre auf Hochschulniveau reguläre Ausdrücke   
../korpus_2025-10-17/llama-4-scout/duck.ai_2025... 1 з 2 - 17.10.2025, 10:48:41    Erkläre einem Kind in der Grundschule reguläre...   
                                                   2 з 2 - 17.10.2025, 10:48:55       Erkläre auf Hochschulniveau reguläre Ausdrücke   
../korpus_2025-10-17/llama-4-scout/duck.ai_2025... 1 von 2 - 17.10.2025, 10:47:03  Erkläre einem Kind in der Grundschule reguläre...   
                                                   2 von 2 - 17.10.2025, 10:47:16    Erkläre auf Hochschulniveau reguläre Ausdrücke.   
../korpus_2025-10-17/llama-4-scout/duck.ai_2025... 1 von 2 - 17.10.2025, 10:49:14  Erkläre einem Kind in der Grundschule reguläre...   
                                                   2 von 2 - 17.10.2025, 10:49:34     Erkläre auf Hochschulniveau reguläre Ausdrücke   
../korpus_2025-10-17/llama-4-scout/duck.ai_2025... 1 von 2 - 17.10.2025, 10:49:01  Erkläre einem Kind in der Grundschule reguläre...   
                                                   2 von 2 - 17.10.2025, 10:49:14     Erkläre auf Hochschulniveau reguläre Ausdrücke   
../korpus_2025-10-17/gpt-4o-mini/duck.ai_2025-1... 1 з 1 - 17.10.2025, 10:44:02    Erkläre einem Kind in der Grundschule reguläre...   
../korpus_2025-10-17/gpt-4o-mini/duck.ai_2025-1... 1 von 2 - 17.10.2025, 10:42:02  Erkläre einem Kind in der Grundschule reguläre...   
                                                   2 von 2 - 17.10.2025, 10:43:14     Erkläre auf Hochschulniveau reguläre Ausdrücke   
../korpus_2025-10-17/gpt-4o-mini/duck.ai_2025-1... 1 von 2 - 17.10.2025, 10:50:23  Erkläre einem Kind in der Grundschule reguläre...   
                                                   2 von 2 - 17.10.2025, 10:50:50     Erkläre auf Hochschulniveau reguläre Ausdrücke   
../korpus_2025-10-17/gpt-4o-mini/duck.ai_2025-1... 1 von 2 - 17.10.2025, 10:38:53  Erkläre einem Kind in der Grundschule reguläre...   
                                                   2 von 2 - 17.10.2025, 10:39:32    Erkläre auf Hochschulniveau reguläre Ausdrücke.   
../korpus_2025-10-17/gpt-4o-mini/duck.ai_2025-1... 1 von 2 - 17.10.2025, 10:39:09  Erkläre einem Kind in der Grundschule reguläre...   
                                                   2 von 2 - 17.10.2025, 10:39:31     Erkläre auf Hochschulniveau reguläre Ausdrücke   
../korpus_2025-10-17/gpt-oss-120b/duck.ai_2025

Füge auf Basis der gesäuberten Antworten die entsprechenden 3-Gramm-Sets hinzu

In [18]:
def n_gram_set(text, n=3):
    """return lowercase n-grams based on text"""
    return { text[i:i+n].lower() for i in range(0, len(text)-n+1) }
#n_gram_set("abcdabc")

In [19]:
corpus_df['3gram'] = corpus_df['cleaned'].apply(n_gram_set)

In [20]:
corpus_df

prompt  \
../korpus_2025-10-17/claude-haiku-3.5/duck.ai_2... 1 von 2 - 17.10.2025, 10:47:25  Erkläre einem Kind in der Grundschule reguläre...   
                                                   2 von 2 - 17.10.2025, 10:47:41     Erkläre auf Hochschulniveau reguläre Ausdrücke   
../korpus_2025-10-17/claude-haiku-3.5/duck.ai_2... 1 з 2 - 17.10.2025, 10:49:54    Erkläre einem Kind in der Grundschule reguläre...   
                                                   2 з 2 - 17.10.2025, 10:50:08       Erkläre auf Hochschulniveau reguläre Ausdrücke   
../korpus_2025-10-17/claude-haiku-3.5/duck.ai_2... 1 von 2 - 17.10.2025, 10:50:30  Erkläre einem Kind in der Grundschule reguläre...   
                                                   2 von 2 - 17.10.2025, 10:50:58     Erkläre auf Hochschulniveau reguläre Ausdrücke   
../korpus_2025-10-17/claude-haiku-3.5/duck.ai_2... 1 von 2 - 17.10.2025, 10:47:34  Erkläre einem Kind in der Grundschule reguläre...   
                                                   2 von 2 - 17.10.2025, 10:47:56     Erkläre auf Hochschulniveau reguläre Ausdrücke   
../korpus_2025-10-17/claude-haiku-3.5/duck.ai_2... 1 von 2 - 17.10.2025, 10:49:33  Erkläre einem Kind in der Grundschule reguläre...   
                                                   2 von 2 - 17.10.2025, 10:49:52    Erkläre auf Hochschulniveau reguläre Ausdrücke.   
../korpus_2025-10-17/llama-4-scout/duck.ai_2025... 1 von 2 - 17.10.2025, 10:45:19  Erkläre einem Kind in der Grundschule reguläre...   
                                                   2 von 2 - 17.10.2025, 10:45:44     Erkläre auf Hochschulniveau reguläre Ausdrücke   
../korpus_2025-10-17/llama-4-scout/duck.ai_2025... 1 з 2 - 17.10.2025, 10:48:41    Erkläre einem Kind in der Grundschule reguläre...   
                                                   2 з 2 - 17.10.2025, 10:48:55       Erkläre auf Hochschulniveau reguläre Ausdrücke   
../korpus_2025-10-17/llama-4-scout/duck.ai_2025... 1 von 2 - 17.10.2025, 10:47:03  Erkläre einem Kind in der Grundschule reguläre...   
                                                   2 von 2 - 17.10.2025, 10:47:16    Erkläre auf Hochschulniveau reguläre Ausdrücke.   
../korpus_2025-10-17/llama-4-scout/duck.ai_2025... 1 von 2 - 17.10.2025, 10:49:14  Erkläre einem Kind in der Grundschule reguläre...   
                                                   2 von 2 - 17.10.2025, 10:49:34     Erkläre auf Hochschulniveau reguläre Ausdrücke   
../korpus_2025-10-17/llama-4-scout/duck.ai_2025... 1 von 2 - 17.10.2025, 10:49:01  Erkläre einem Kind in der Grundschule reguläre...   
                                                   2 von 2 - 17.10.2025, 10:49:14     Erkläre auf Hochschulniveau reguläre Ausdrücke   
../korpus_2025-10-17/gpt-4o-mini/duck.ai_2025-1... 1 з 1 - 17.10.2025, 10:44:02    Erkläre einem Kind in der Grundschule reguläre...   
../korpus_2025-10-17/gpt-4o-mini/duck.ai_2025-1... 1 von 2 - 17.10.2025, 10:42:02  Erkläre einem Kind in der Grundschule reguläre...   
                                                   2 von 2 - 17.10.2025, 10:43:14     Erkläre auf Hochschulniveau reguläre Ausdrücke   
../korpus_2025-10-17/gpt-4o-mini/duck.ai_2025-1... 1 von 2 - 17.10.2025, 10:50:23  Erkläre einem Kind in der Grundschule reguläre...   
                                                   2 von 2 - 17.10.2025, 10:50:50     Erkläre auf Hochschulniveau reguläre Ausdrücke   
../korpus_2025-10-17/gpt-4o-mini/duck.ai_2025-1... 1 von 2 - 17.10.2025, 10:38:53  Erkläre einem Kind in der Grundschule reguläre...   
                                                   2 von 2 - 17.10.2025, 10:39:32    Erkläre auf Hochschulniveau reguläre Ausdrücke.   
../korpus_2025-10-17/gpt-4o-mini/duck.ai_2025-1... 1 von 2 - 17.10.2025, 10:39:09  Erkläre einem Kind in der Grundschule reguläre...   
                                                   2 von 2 - 17.10.2025, 10:39:31     Erkläre auf Hochschulniveau reguläre Ausdrücke   
../korpus_2025-10-17/gpt-oss-120b/duck.ai_2025

## StyloMetrix

ACHTUNG: Erfordert spezielle Installation, läuft hier im BASE-Environment nicht durch

```
import stylo_metrix as sm

# example texts
example_texts = [ 
    # jbusse
    """Im Rahmen von Forschungs und Lehre müssen Leistungen individuell zuschreibbar sein. 
Aber auch moderne generative KI kann inzwischen Texte generieren. 
Problem: Bei einem einem “gut formulierten” Text ist es sehr schwer zu unterscheiden,
*   ob der Text ein von der KI generierter Text ist, den ein Mensch in Auftrag gegeben hat, oder
*   ob der Text ein vom Menschen selbst formulierter Rohtext ist, der von der KI lektoriert wurde.""",
    """Unser Prüfungsrecht verlangt, dass eine Leistung individuell zugeschrieben werden kann. 
Die KI-Leitlinie Bayern verlangt, dass KI-generierte Inhalte eindeutig gekennzeichnet werden. 
Es stellt sich die Frage, wie man in Studienarbeiten und Bachelorabeiten, 
aber auch Präsentationen etc. die Beiträge von KI auch typografisch kenntlich machen kann. """,
    # ChatGPT
    """In der Forschung und Lehre muss man wissen, wer etwas geschrieben hat. 
Aber heutzutage kann auch KI Texte erstellen.
Das Problem: Wenn ein Text gut geschrieben ist, kann man kaum erkennen, ob
* der Text von einer KI stammt, die jemand beauftragt hat, oder
* der Text zuerst von einem Menschen geschrieben und dann von der KI verbessert wurde.""",
    """Das Prüfungsrecht verlangt, dass man genau erkennen kann, wer eine Leistung erbracht hat.
Die KI-Leitlinie Bayern fordert, dass KI-generierte Inhalte klar gekennzeichnet werden.
Die Frage ist nun, wie man in Studienarbeiten, Bachelorarbeiten oder auch in Präsentationen zeigen kann, 
welche Teile von der KI stammen – auch durch die Gestaltung des Textes."""
    ]

example_stylo = sm.StyloMetrix('de') # define langauge, one of ('de','en', 'pl', 'ru', 'ukr')
example_metrics_df = example_stylo.transform(example_texts)
example_metrics_df
```


(ipynb)=
## ipynb

In [21]:
class Ipynb():
    def __init__(self, file_location):
        with open(file_location, 'r') as f:
            self.nb_json = json.load(f)
        print(f"{file_location=}, {len(self.nb_json)=}")
        
        self.file_location = file_location
        self.cell_dict = {}
        self.count = 0
        
        for cell in self.nb_json['cells']:
            print(f"\n{self.count=}, {cell=}") # ist ein dict
            cell_id = (self.file_location, f"{self.count}")
            self.cell_dict[cell_id] = cell
            self.count += 1
            
        # our data structure is fine if the following statement gives a meaningful result
        self.df = pd.DataFrame.from_dict(self.cell_dict, orient="index")

In [22]:
hw = Ipynb("HalloWelt.ipynb")

file_location='HalloWelt.ipynb', len(self.nb_json)=4

self.count=0, cell={'cell_type': 'markdown', 'id': '77a931b0-1ca0-4df3-8c96-b5857278603a', 'metadata': {}, 'source': ['# Hallo Welt!']}

self.count=1, cell={'cell_type': 'code', 'execution_count': 5, 'id': '650b7c22-be13-4481-b425-3482ef578a55', 'metadata': {}, 'outputs': [], 'source': ['# Die Antwort auf alle Fragen\n', 'sechs, sieben = 6, 7\n', 'antwort = sechs * sieben']}

self.count=2, cell={'cell_type': 'code', 'execution_count': 6, 'id': 'b96945c1-2972-4868-af2e-9e1da6e6a556', 'metadata': {}, 'outputs': [{'name': 'stdout', 'output_type': 'stream', 'text': ['antwort=42\n']}], 'source': ['print(f"{antwort=}")']}

self.count=3, cell={'cell_type': 'raw', 'id': '98ca59a1-d389-48c2-8cb0-e72329277864', 'metadata': {}, 'source': ['Wozu benötigt man raw Zellen?']}

self.count=4, cell={'cell_type': 'code', 'execution_count': None, 'id': '5ac153f1-9a60-4eda-8d65-a32f382f9980', 'metadata': {}, 'outputs': [], 'source': []}


In [23]:
hw.df

cell_type                                    id metadata  \
HalloWelt.ipynb 0  markdown  77a931b0-1ca0-4df3-8c96-b5857278603a       {}   
                1      code  650b7c22-be13-4481-b425-3482ef578a55       {}   
                2      code  b96945c1-2972-4868-af2e-9e1da6e6a556       {}   
                3       raw  98ca59a1-d389-48c2-8cb0-e72329277864       {}   
                4      code  5ac153f1-9a60-4eda-8d65-a32f382f9980       {}   

                                                              source  \
HalloWelt.ipynb 0                                    [# Hallo Welt!]   
                1  [# Die Antwort auf alle Fragen\n, sechs, siebe...   
                2                             [print(f"{antwort=}")]   
                3                    [Wozu benötigt man raw Zellen?]   
                4                                                 []   

                   execution_count  \
HalloWelt.ipynb 0              NaN   
                1              5.0   
                2              6.0   
                3              NaN   
                4              NaN   

                                                             outputs  
HalloWelt.ipynb 0                                                NaN  
                1                                                 []  
                2  [{'name': 'stdout', 'output_type': 'stream', '...  
                3                                                NaN  
                4                                                 []